# Synthetic Generation of a Corporate Ratings Dataset

In [17]:
%pylab inline
import pandas as pd
import os
import s3fs

Populating the interactive namespace from numpy and matplotlib


In [18]:
import boto3
import sagemaker
from smfinance import SECDataSetConfig, DataLoader

S3_BUCKET_NAME = "gecko-examples-beta"
S3_FOLDER_NAME = "CCR_Synthetic"

In [19]:
%%time
df1 = pd.read_csv('s3://gecko-examples-beta/NB3_SEC_IndustryClassification/sec_ind_test.csv')
fn = 's3://' + S3_BUCKET_NAME + '/' + S3_FOLDER_NAME + '/mdna_ind.csv'
df1.to_csv(fn, index=False)
df1.head()

CPU times: user 7.66 s, sys: 912 ms, total: 8.57 s
Wall time: 16.9 s


MDNA industry_code
0    MANAGEMENT'S DISCUSSION AND ANALYSIS OF FINA...             E
1     Management's Discussion and Analysis of Fin...             D
2     MANAGEMENT'S DISCUSSION AND ANALYSIS OF FIN...             B
3      Management's Discussion and Analysis of Fi...             B
4     Management's Discussion and Analysis of Fin...             D

In [5]:
!aws s3 cp s3://gecko-jumpstart/smfinance-0.0.1-py3-none-any.whl ./

download: s3://gecko-jumpstart/smfinance-0.0.1-py3-none-any.whl to ./smfinance-0.0.1-py3-none-any.whl


In [6]:
!pip install smfinance-0.0.1-py3-none-any.whl

/opt/conda/lib/python3.7/site-packages/secretstorage/dhcrypto.py:16: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
/opt/conda/lib/python3.7/site-packages/secretstorage/util.py:25: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
Processing ./smfinance-0.0.1-py3-none-any.whl
smfinance is already installed with the same version as the provided wheel. Use --force-reinstall to force an installation of the wheel.
You should consider upgrading via the '/opt/conda/bin/python -m pip install --upgrade pip' command.


In [15]:
%%time
# Example 1
from smfinance import NLPScoreConfig, NLPScore, NLPScoreType

nlp_score_processor = NLPScore(
        sagemaker.get_execution_role(),         # loading job execution role
        16,                                      # number of ec2 instances to run the loading job, can support multiple instances
        'ml.c5.2xlarge',                        # ec2 instance type to run the loading job
        volume_size_in_gb=30,                   # size in GB of the EBS volume to use
        volume_kms_key=None,                    # KMS key for the processing volume
        output_kms_key=None,                    # KMS key ID for processing job outputs
        max_runtime_in_seconds=None,            # timeout in seconds. Default is 24 hours.
        sagemaker_session=sagemaker.Session(),  # session object
        tags=None)                              # a list of key-value pairs

score_types = [NLPScoreType.POSITIVE, NLPScoreType.NEGATIVE, NLPScoreType.LITIGIOUS, NLPScoreType.POLARITY,
               NLPScoreType.RISK, NLPScoreType.READABILITY, NLPScoreType.FRAUD, NLPScoreType.SAFE, 
               NLPScoreType.CERTAINTY, NLPScoreType.UNCERTAINTY, NLPScoreType.SENTIMENT]

nlp_config = NLPScoreConfig(score_types,                                  # list of score types
                    's3://{}/{}'.format(S3_BUCKET_NAME, S3_FOLDER_NAME),  # output s3 prefix (both bucket and folder names are required)
                    'CCR_synthetic_text_nlp_scores.csv')                  # output file name

nlp_score_processor.calculate(
    nlp_config,                                                       # nlp score config
    'MDNA',                                                           # the column name of the file needs to be scored
    s3_bucket=S3_BUCKET_NAME,                                         # the S3 bucket for the file to be summarized
    s3_key='{}/{}'.format(S3_FOLDER_NAME, 'mdna_ind.csv'))            # the S3 key for the file to be summarized


2021-07-16 01:08:59,077 : INFO : Downloading CCR_Synthetic/mdna_ind.csv to /tmp/tmpjhqsoyma/s3_data.csv
2021-07-16 01:09:00,170 : INFO : Downloaded CCR_Synthetic/mdna_ind.csv to /tmp/tmpjhqsoyma/s3_data.csv
2021-07-16 01:09:00,172 : INFO : Sharding data from /tmp/tmpjhqsoyma/s3_data.csv to /tmp/tmpjhqsoyma/shards
2021-07-16 01:09:05,848 : INFO : Completed sharding data from /tmp/tmpjhqsoyma/s3_data.csv to /tmp/tmpjhqsoyma/shards
2021-07-16 01:09:06,033 : INFO : Starting SageMaker processing job to calculate NLP scores
2021-07-16 01:09:06,034 : INFO : You are not charged when EC2 instances are in pending state
2021-07-16 01:09:06,035 : INFO : More info: https://docs.aws.amazon.com/AWSEC2/latest/UserGuide/ec2-instance-lifecycle.html
2021-07-16 01:09:27,731 : INFO : Creating processing-job with name jumpstart-gecko-nlp-score-2021-07-16-01-09-06-036



Job Name:  jumpstart-gecko-nlp-score-2021-07-16-01-09-06-036
Inputs:  [{'InputName': 'config', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-us-west-2-043480434002/jumpstart-gecko-nlp-score-2021-07-16-01-09-06-036/input/config', 'LocalPath': '/opt/ml/processing/input/config', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'FullyReplicated', 'S3CompressionType': 'None'}}, {'InputName': 'input-2', 'AppManaged': False, 'S3Input': {'S3Uri': 's3://sagemaker-us-west-2-043480434002/jumpstart-gecko-nlp-score-2021-07-16-01-09-06-036/input/input-2', 'LocalPath': '/opt/ml/processing/input/data', 'S3DataType': 'S3Prefix', 'S3InputMode': 'File', 'S3DataDistributionType': 'ShardedByS3Key', 'S3CompressionType': 'None'}}]
Outputs:  [{'OutputName': 'output-1', 'AppManaged': False, 'S3Output': {'S3Uri': 's3://sagemaker-us-west-2-043480434002/jumpstart-gecko-nlp-score-2021-07-16-01-09-05-848/CCR_synthetic_text_nlp_scores.csv_gecko_internal', 'LocalPath': '/opt/ml/

2021-07-16 03:30:15,428 : INFO : Merging processing job output
2021-07-16 03:30:28,383 : INFO : Merged processing job output
2021-07-16 03:30:28,384 : INFO : Completed SageMaker processing job to calculate NLP scores


CPU times: user 1min 16s, sys: 9.1 s, total: 1min 25s
Wall time: 2h 21min 29s


In [21]:
df2 = pd.read_csv('CCR_synthetic_text_nlp_scores.csv')
print(df2.shape)
df2

(3286, 13)


MDNA industry_code  \
0      MANAGEMENT'S DISCUSSION AND ANALYSIS OF FINAN...             H   
1      Management's Discussion and Analysis of Finan...             D   
2       Management's Discussion and Analysis of Fina...             H   
3      "Management's Discussion and Analysis of Fina...             D   
4      Management’s Discussion and Analysis of Finan...             D   
...                                                 ...           ...   
3281   Management’s Discussion and Analysis of Finan...             D   
3282   MANAGEMENT’S DISCUSSION AND ANALYSIS OF FINAN...             I   
3283    MANAGEMENT'S DISCUSSION AND ANALYSIS OF FINA...             E   
3284   Management’s Discussion and Analysis of Finan...             I   
3285   Management's Discussion and Analysis of Finan...             G   

      certainty     fraud  litigious  negative  polarity  positive  \
0      0.037973  0.024456   0.022701 -0.024456  0.508808  0.075121   
1      0.041008  0.034980   0.029592 -0.028404  0.493073  0.083661   
2      0.033996  0.040126   0.037526 -0.028516  0.531298  0.093164   
3      0.035461  0.051221   0.052797 -0.052797  0.234286  0.085106   
4      0.039932  0.033259   0.027857 -0.030505  0.523179  0.097447   
...         ...       ...        ...       ...       ...       ...   
3281   0.029868  0.039693   0.040086 -0.027510  0.519726  0.087051   
3282   0.034457  0.024824   0.025195 -0.033160  0.424437  0.082067   
3283   0.035264  0.034425   0.032186 -0.032186  0.493392  0.094878   
3284   0.033378  0.029145   0.035035 -0.034974  0.400946  0.081789   
3285   0.026792  0.025452   0.033713 -0.029471  0.476190  0.083054   

      readability      risk      safe  sentiment  uncertainty  
0     3846.808333  0.036735  0.037251      0.081     0.018471  
1     4338.103271  0.047036  0.057174      0.051     0.019910  
2     4242.693973  0.041612  0.064555      0.070     0.022292  
3      516.687747  0.095351  0.060678      0.010     0.041765  
4     3746.336252  0.043639  0.067366      0.079     0.026586  
...           ...       ...       ...        ...          ...  
3281  2029.354455  0.042051  0.059147      0.081     0.019454  
3282  2121.489188  0.053538  0.052612      0.119     0.027788  
3283  1417.987965  0.051777  0.049258      0.073     0.027428  
3284  6447.140727  0.048656  0.062830      0.104     0.026874  
3285  1777.836635  0.041081  0.052690      0.102     0.020094  

[3286 rows x 13 columns]